In [1]:
import kagglehub
from pyspark.sql import SparkSession
import pyspark.sql.functions as F
from pyspark.sql.window import Window
from pyspark.sql.types import StructType, StructField, StringType, DoubleType, IntegerType
from pyspark.rdd import RDD
from pyspark.ml.feature import MinMaxScaler, VectorAssembler
from collections import deque
import matplotlib.pyplot as plt
import numpy as np
import mlflow
import mlflow.keras
import pandas as pd
import tensorflow as tf
import os
import math
import json

2025-10-02 15:11:47.843353: I external/local_xla/xla/tsl/cuda/cudart_stub.cc:31] Could not find cuda drivers on your machine, GPU will not be used.
2025-10-02 15:11:47.843601: I tensorflow/core/util/port.cc:153] oneDNN custom operations are on. You may see slightly different numerical results due to floating-point round-off errors from different computation orders. To turn them off, set the environment variable `TF_ENABLE_ONEDNN_OPTS=0`.
2025-10-02 15:11:47.874277: I tensorflow/core/platform/cpu_feature_guard.cc:210] This TensorFlow binary is optimized to use available CPU instructions in performance-critical operations.
To enable the following instructions: AVX2 AVX512F AVX512_VNNI AVX512_BF16 FMA, in other operations, rebuild TensorFlow with the appropriate compiler flags.
2025-10-02 15:11:48.569364: I tensorflow/core/util/port.cc:153] oneDNN custom operations are on. You may see slightly different numerical results due to floating-point round-off errors from different computation or

# Demonstration of AI for Stock Predictions and Discussions Why It Fails
* **Author:** Dr. Dierck Matern
* **e-mail:** dierck.matern\[at\]dmatern-freelancing.com

## Introduction
Stocks are very interesting time series.
Not only do they have huge impact on our life, they also have very interesting statistical properties.
As time series, they provide samples per time: for each time stamp $t$, we can say that there is a price $p(t)$, at least from opening to closing of the stock exchange.
Then, the following sample is very close to the previous one, that is, $p(t + \delta) \approx p(t)$ for small enough $\delta$.
However, that is about all they share with traditional signals, like audio (here, the $\delta$ relates to the highest frequencies), molecular movements (here it depends on temperature), temperature curves, pressures, etc.
Those signals have the property that they behave the same tomorrow as they do today.
But if the stock market would work that way, somebody would have figured out to exploit it, which then results in a change of rules.
This is why you should always take financial advice for investment with a grain of salt.

But let's pretend we wouldn't know that.
It is very promissing to train an artificial intelligence system to optimize our income, isn't it?
This is known as "[algorithmic trading](https://en.wikipedia.org/w/index.php?title=Algorithmic_trading&oldid=1312696669)".
There are very sophisticated algorithms developed for this purpose.

A very well developed algorithm for time series which became popular in the last decade or so is LSTM, or long short-term memory.
Though transformer networks are state of the art in many applications, for shorter sequences (just a dozen ticks or two) or multivariate data, they still are a go-to algorithm.
Those are neural networks which overcome weaknesses in classical recurrent neural networks by including memory and forgetting cells, called "gates".
The gates are, basically, neural networks on their own.
LSTMs learn patterns in time dependent signals by adapting all the weights, for the time series as well as for the gates, to remember how much of the past is stored and then utilized to make a prediction.
Please notice that a "prediction" in this context simply means an estimated value which has not been measured yet - it is, not necessarily, a prediction in time, though this would be a very good example of what LSTMs are capable of.

In the following, we will ignore that stock prices are not good examples for easy signal processing.
The goal is to discuss the properties that prevent LSTMs from performing well on the data set.

And if it isn't obvious, this is no financial advice.
If there is some advise to take from this short experiment, it is to not do it like discussed here.

## Preparation
First, we establish some constants to be used in the progress.

In [2]:
# some column name constants to prevent typos
DATE_COL: str = "date_col"
RATIO: str = "ratio"
STOCK_NAME: str = "stock_name"
OPEN: str = "open"
CLOSE: str = "close"
COUNT: str = "count"
ROW_NUM: str = "row_num"
PREDICTION: str = "prediction"
SCALER: str = "scaler"
MODEL: str = "model"
ERROR: str = "error"
PREDICTION_ARRAY: str = "prediction_array"
TRAIN_ARRAY: str = "train_array"
INVESTMENT: str = "investment"
STOCK_VALUE: str = "stock_value"

MIN_SAMPLE_SIZE: int = 1000
TRAIN_RATIO: float = 0.7  # how much of the data is for training
VALID_RATIO: float = 0.15  # how much is for validation
SEQUENCE_LENGTH: int = 21  # Length of the sequence for LSTM training
BATCH_SIZE: int = 32  # Batch size
STOCK_NAME: str = "stock_name"  # Stock column name
SCHEMA: StructType = StructType([
    StructField("", IntegerType(), False),
    StructField("company_name", StringType(), False),
    StructField("stock_name", StringType(), False),
    StructField("date", StringType(), False),
    StructField("open", DoubleType(), True),
    StructField("high", DoubleType(), True),
    StructField("low", DoubleType(), True),
    StructField("close", DoubleType(), True),
    StructField("volume", IntegerType(), True)
])
HEADER: list[str] = ["index", "company_name", "stock_name", "date", "open", "high", "low", "close", "volume"]
PATIENCE: int = 3
EPOCHS: int = 100

# Design parameter for plotting
GRIDWIDTH: int = 3

# Storage files MLFlow.
RUN_ID_FILE: str = "StockRunIds.json"

We are using Apache Spark for managing the data here.
Reason is that it is a good data management framework, it has no direct impact on the evaluation.

In [3]:
spark = (
    SparkSession.builder
    .appName("Semiconductor")
    .config("spark.memory.offHeap.enabled", "true")
    .config("spark.memory.offHeap.size", "10g")
    .getOrCreate()
)

Using Spark's default log4j profile: org/apache/spark/log4j2-defaults.properties
25/10/02 15:11:49 WARN Utils: Your hostname, laptop, resolves to a loopback address: 127.0.1.1; using 192.168.178.43 instead (on interface wlp2s0)
25/10/02 15:11:49 WARN Utils: Set SPARK_LOCAL_IP if you need to bind to another address
Using Spark's default log4j profile: org/apache/spark/log4j2-defaults.properties
Setting default log level to "WARN".
To adjust logging level use sc.setLogLevel(newLevel). For SparkR, use setLogLevel(newLevel).
25/10/02 15:11:49 WARN NativeCodeLoader: Unable to load native-hadoop library for your platform... using builtin-java classes where applicable


Loading the data set from Kaggle.
This is a small data set and will suffice for the experiment.

In [4]:
# getting some test data
path: str = kagglehub.dataset_download("farukece/semiconductor-stocks-and-the-ai-surge")
file_path: str = os.path.join(path, os.listdir(path)[0])
assert os.path.isfile(file_path)

Open the data set.
Some names include a "newline" character, possibly because of an automated script to generate the original data set.
Hence, we need the "multiline" option here or would not be able to parse the file correctly.

Furthermore, the date is, so far, ensured to be a string.
It is converted to a date in a new column.

In [5]:
df = spark.read.option("multiline", "true").csv(file_path, header=True, schema=SCHEMA).toDF(*HEADER)  # ignoring the header warning, this is a Kaggle data set which is a bit off
df = df.withColumn('date', F.col('date').cast('string'))
df = df.withColumn(DATE_COL, F.to_date(F.col('date'))).filter(F.col(DATE_COL).isNotNull())

In [6]:
stock_counts = df.groupBy(STOCK_NAME).agg(F.count('*').alias(COUNT)).filter(F.col(COUNT) > MIN_SAMPLE_SIZE)
df_filtered = df.join(stock_counts, on=STOCK_NAME, how="inner")

Here, we add the target value: the stock price changes.
If the stock opens low and ends high, the price has increased.
We ignore prices outside of trading days; if you want to use that, you could simply put a delay on the closing price and use that one instead the opening price.
Furthermore, we take the logarithm of these values; that way, the prices and changes are independent of the price of a single share, but only on the relative change.

In [7]:
df_filtered = df_filtered.withColumn(DATE_COL, F.to_date(F.col('date'))).filter(F.col(DATE_COL).isNotNull())
df_filtered = df_filtered.withColumn(RATIO, F.log(F.col(CLOSE)) - F.log(F.col(OPEN)))
stock_names = df_filtered.select(STOCK_NAME).distinct()

Creating the sequences for training, validation, and testing.
Using generators is memory efficient.

Notice that the reapeat function at for the `to_tf_dataset` function has some implications for the implementation later on.
Nevertheless, it makes sure that we do not run out of data.

In [8]:
def sequence_generator(rdd: RDD, seq_length: int = SEQUENCE_LENGTH,
                       batch_size: int = BATCH_SIZE):
    buffer = deque(maxlen=seq_length + 1)
    X_batch, y_batch = [], []

    for val in rdd.toLocalIterator():
        buffer.append(val)
        if len(buffer) == seq_length + 1:
            X = np.array(list(buffer)[:-1]).reshape(seq_length, 1)
            y = np.array([buffer[-1]])
            X_batch.append(X)
            y_batch.append(y)
            if len(X_batch) == batch_size:
                yield np.array(X_batch, dtype=np.float32), np.array(y_batch, dtype=np.float32)
                X_batch, y_batch = [], []

    if X_batch:
        yield np.array(X_batch, dtype=np.float32), np.array(y_batch, dtype=np.float32)

In [9]:
def to_tf_dataset(generator, seq_length: int = SEQUENCE_LENGTH, batch_size: int = BATCH_SIZE):
    dataset = tf.data.Dataset.from_generator(
        generator,
        output_signature=(
            tf.TensorSpec(shape=(None, seq_length, 1), dtype=tf.float32),
            tf.TensorSpec(shape=(None, 1), dtype=tf.float32)
        )
    ).repeat()
    return dataset

Now we are training the models.
The data sets are split in training, validation and testing sets, as is good practice.
This code also saves the data using `MLFlow` for reproducability.

Output of the LSTM is bound to the sequence length since those are connected anyway.
The about $20 \%$ is a good practice. 

In [10]:
w = Window.partitionBy(STOCK_NAME).orderBy(F.col(DATE_COL))
assembler = VectorAssembler(inputCols=[RATIO], outputCol="features_vec")
scaler = MinMaxScaler(inputCol="features_vec", outputCol="scaled_features")

simple_packages = {}


def extract(row):
    return float(row.scaled_features[0])


if os.path.isfile(RUN_ID_FILE):
    with open(RUN_ID_FILE, 'r') as f:
        run_ids = json.load(f)
else:
    run_ids = {}

for stock_name in stock_names.rdd.toLocalIterator():
    stock = stock_name[STOCK_NAME]
    full_data = df_filtered.where(F.col(STOCK_NAME) == stock) \
        .orderBy(F.col(DATE_COL)) \
        .withColumn(ROW_NUM, F.row_number().over(w)) \
        .select(F.col(OPEN), F.col(CLOSE), F.col(DATE_COL), F.col(RATIO), F.col(ROW_NUM))
    n_samples = full_data.count()
    n_train = int(TRAIN_RATIO * n_samples)
    n_valid = int(VALID_RATIO * n_samples)
    full_vector = assembler.transform(full_data)
    scaler_model = scaler.fit(full_vector.where(F.col(ROW_NUM) <= n_train))
    full_scaled = scaler_model.transform(full_vector)
    train_data = (
        full_scaled.where(F.col(ROW_NUM) <= n_train)
        .rdd.map(extract)
    )
    val_data = (
        full_scaled.where(
            (F.col(ROW_NUM) > n_train) & (F.col(ROW_NUM) <= n_train + n_valid)
        ).rdd.map(extract)
    )
    test_data = (
        full_scaled.where(F.col(ROW_NUM) > n_train + n_valid)
        .rdd.map(extract)
    )
    train_dataset = to_tf_dataset(lambda: sequence_generator(train_data))
    val_dataset = to_tf_dataset(lambda: sequence_generator(val_data))
    test_dataset = to_tf_dataset(lambda: sequence_generator(test_data))
    artifact_path = f"model_{stock.replace('.', '')}"
    if stock not in run_ids:
        print(f"Stock {stock} not found, trianing")
        with mlflow.start_run(run_name=stock) as run:
            model = tf.keras.Sequential([
                tf.keras.layers.Input(shape=(SEQUENCE_LENGTH, 1)),
                tf.keras.layers.LSTM(math.floor(SEQUENCE_LENGTH / 5.0)),
                tf.keras.layers.Dense(1)
            ])
            model.compile(optimizer="adam", loss="mse")
            early_stop = tf.keras.callbacks.EarlyStopping(
                monitor="val_loss",
                patience=PATIENCE,
                restore_best_weights=True
            )
            print(f"fitting {stock}... ", end='', flush=True)
            history = model.fit(train_dataset,
                                validation_data=val_dataset,
                                epochs=EPOCHS,
                                steps_per_epoch=math.ceil((n_train - SEQUENCE_LENGTH) / BATCH_SIZE),
                                validation_steps=math.ceil((n_valid - SEQUENCE_LENGTH) / BATCH_SIZE),
                                callbacks=[early_stop],
                                verbose=0)
            print("done.")
            mlflow.log_param("stock_symbol", stock)
            mlflow.log_param("epochs", EPOCHS)
            loss = model.evaluate(train_dataset, verbose=0, steps=math.ceil((n_train - SEQUENCE_LENGTH) / BATCH_SIZE))
            mlflow.log_metric("loss", loss)
            # using input_example is currently broken, we create a manual signature
            input_spec = mlflow.types.schema.TensorSpec(
                shape=(-1, SEQUENCE_LENGTH, 1),
                type=np.dtype(np.float32),
                name="input_1"
            )
            output_spec = mlflow.types.schema.TensorSpec(
                shape=(-1, 1),
                type=np.dtype(np.float32),
                name="output_1"
            )
            signature = mlflow.models.signature.ModelSignature(
                inputs=mlflow.types.schema.Schema([input_spec]),
                outputs=mlflow.types.schema.Schema([output_spec])
            )
            mlflow.keras.log_model(model,
                                   name=artifact_path,
                                   signature=signature)
            run_ids[stock] = run.info.run_id
    else:
        print(f"Pretrained model {stock} found, loading.")
        model = mlflow.keras.load_model(f"runs:/{run_ids[stock]}/{artifact_path}")

    diff = []
    y_hat_full = [0.0] * SEQUENCE_LENGTH
    orig_min = scaler_model.originalMin[0]
    orig_max = scaler_model.originalMax[0]
    diff_train = []
    y_train_hat_full = [0.0] * SEQUENCE_LENGTH

    def inverse_transform(x):
        return x * (orig_max - orig_min) + orig_min

    for X_test, y_test in sequence_generator(test_data):
        y_hat = model.predict(X_test, verbose=0)
        y_diff = y_test - y_hat
        for y_d, y_h in zip(y_diff, y_hat):
            diff.append(y_d.item()**2)
            y_hat_full.append(inverse_transform(y_h.item()))

    for X_train, y_train in sequence_generator(train_data):
        y_hat = model.predict(X_train, verbose=0)
        y_diff = y_train - y_hat
        for y_d, y_h in zip(y_diff, y_hat):
            diff_train.append(y_d.item()**2)
            y_train_hat_full.append(inverse_transform(y_h.item()))

    test_df = full_data.where(F.col(ROW_NUM) > n_train + n_valid).toPandas()
    test_df[PREDICTION] = y_hat_full
    train_df = full_data.where(F.col(ROW_NUM) <= n_train).toPandas()
    train_df[PREDICTION] = y_train_hat_full

    package = {
        SCALER: scaler_model,
        MODEL: model,
        ERROR: np.mean(diff),
        PREDICTION_ARRAY: test_df,
        TRAIN_ARRAY: train_df
    }
    simple_packages[stock] = package

if os.path.isfile(RUN_ID_FILE):
    os.remove(RUN_ID_FILE)

with open(RUN_ID_FILE, 'a') as f:
    json.dump(run_ids, f)

Pretrained model 688608.SS found, loading.


2025-10-02 15:11:56.888017: E external/local_xla/xla/stream_executor/cuda/cuda_platform.cc:51] failed call to cuInit: INTERNAL: CUDA error: Failed call to cuInit: UNKNOWN ERROR (303)


Pretrained model 603986.SS found, loading.


Pretrained model ASYS found, loading.


Pretrained model TSM found, loading.


...

Pretrained model WAF.F found, loading.


Pretrained model 6857.T found, loading.


Pretrained model PLAB found, loading.


Pretrained model BRN.AX found, loading.


Pretrained model LASR found, loading.


## Evaluation
Now we have trained models, we need a strategy how we use the models.
The theory is simple: we want to buy stocks when they will rise and sell when they will fall.
And the larger the change, the more we want to alter our current investment.
Hence, we can simply scale the investment to the magnitude as well.

We compare the prediction of the training and the test set.

In [11]:
def fill_ai_trader_returns(data_frame: pd.DataFrame, invest_value: float = 1000.0):
    total_spent = [0.0] * len(data_frame)
    stock_value = [0.0] * len(data_frame)
    open_value = data_frame[OPEN]
    close_value = data_frame[CLOSE]
    prediction = data_frame[PREDICTION]
    last_stock_value = 0.0  # for t = 0, we save current stock value also separately
    for t in range(0, len(prediction)):
        current_prediction = prediction[t]
        investment = current_prediction * invest_value
        if investment + last_stock_value < 0:
            investment = -last_stock_value
        stock_value[t] = investment
        total_spent[t] = investment
        if t > 0:
            stock_value[t] += stock_value[t - 1]
            total_spent[t] += total_spent[t - 1]

        ratio = close_value[t] / open_value[t]  # no value of stock is 0, that would be totally worthless
        stock_value[t] = ratio * stock_value[t]
        last_stock_value = stock_value[t]

    data_frame[INVESTMENT] = total_spent
    data_frame[STOCK_VALUE] = stock_value

In [12]:
fig, axs = plt.subplots(len(simple_packages), 2, figsize=(15, 3 * len(simple_packages)))

for h, data_package in enumerate(simple_packages.items()):
    name, package = data_package
    fill_ai_trader_returns(package[TRAIN_ARRAY])
    fill_ai_trader_returns(package[PREDICTION_ARRAY])
    d_time_train = package[TRAIN_ARRAY][DATE_COL][SEQUENCE_LENGTH+1:-1]
    d_time_test = package[PREDICTION_ARRAY][DATE_COL][SEQUENCE_LENGTH+1:-1]
    d_money_train = package[TRAIN_ARRAY][STOCK_VALUE][SEQUENCE_LENGTH+1:-1] \
        - package[TRAIN_ARRAY][INVESTMENT][SEQUENCE_LENGTH+1:-1]
    d_money_test = package[PREDICTION_ARRAY][STOCK_VALUE][SEQUENCE_LENGTH+1:-1] \
        - package[PREDICTION_ARRAY][INVESTMENT][SEQUENCE_LENGTH+1:-1]
    ax = axs[h, 0]
    ax.fill_between(d_time_train, d_money_train, 0,
                    where=(d_money_train > 0), color='green', alpha=0.5)
    ax.fill_between(d_time_train, d_money_train, 0,
                    where=(d_money_train < 0), color='red', alpha=0.5)
    ax.axhline(0, color='gray', linewidth=1)
    ax.plot(d_time_train, d_money_train, color='black', linewidth=2)
    ax.set_title("Train data: " + name)
    ax.set_ylabel("value")
    ax.set_xlabel("time")
    ax = axs[h, 1]
    ax.fill_between(d_time_test, d_money_test, 0,
                    where=(d_money_test > 0), color='green', alpha=0.5)
    ax.fill_between(d_time_test, d_money_test, 0,
                    where=(d_money_test < 0), color='red', alpha=0.5)
    ax.axhline(0, color='gray', linewidth=1)
    ax.plot(d_time_test, d_money_test, color='black', linewidth=2)
    ax.set_title("Test data: " + name)
    ax.set_ylabel("value")
    ax.set_xlabel("time")

fig.tight_layout()
plt.show()

## Interpretation

Okay, what do we see here?
In the left column, we see how much money we earn or lose with the strategy.
Many times, we would lose money even though that is the very data the LSTM is trained on.
The test data performs even worse.

So what did we do wrong?
Are LSTMs bad for prediction, did we use wrong parameters?
We violated one of the rules of data science: we did not include domain knowledge.

Stock prices are riddled with external impact factors.
In fact, they represent the result of changes in the real world, inflicted by a big factor of gambling.
If a business performs well, we assume that the stock price raises.
At least if the performance is as good or even better than estimates, provided by business insiders.
So we have the performance of the company, the estimate of experts, and people who would bet for or against these experts which dominate the stock market.

Even though we cannot include the gamblers in the equation, we would be able to take the experts and the performance of the company into account, this is public information (even though, the experts opinions are often behind a paywall).
Furthermore, we know that certain stocks are correlated, positively or negatively.
Modern algorithms include all of this information as well and are pretty good in predicting prices in a general manner, though not exactly.
Even they struggle from immediate events, like natural desasters, but those events are rare.

So what did the LSTM try to do?
It wanted to find patterns in the training data.
That means, the future performance of the stock price would have been somewhat predictable.
Of course, we could have looked at the residuals to find out that this doesn't work, but only if we have something to compare with, so that is why we didn't do that.
The model of investment was considered more relatable, that is why we put it right into the evaluation.

This example was written to show that time series analysis is not easy, though the implementation might be.
We did not do any parameter optimiztion which would might have changed the results, and we did not boost them by using correlated stocks as well.
This would have been beyond the point: AI cannot solve all problems easily.
Furthermore, this document is made to demonstrate how to use the packages, especially MLFlow and Spark.
In that way, at least the most important functions can be found here as well.